In [1]:
from netgen.csg import *
from ngsolve import *
import numpy as np
H_MAX: float = 0.2  # Determines how fine the mesh should be.

In [2]:
def MakeGeometry():  # this makes a box, with labelled faces
    geometry = CSGeometry()
    left = Plane(Pnt(0, 0, 0), Vec(-1, 0, 0)).bc("left")
    right = Plane(Pnt(1, 1, 1), Vec(1, 0, 0)).bc("right")
    front = Plane(Pnt(0, 0, 0), Vec(0, -1, 0)).bc("front")
    back = Plane(Pnt(1, 1, 1), Vec(0, 1, 0)).bc("back")
    bot = Plane(Pnt(0, 0, 0), Vec(0, 0, -1)).bc("bot")
    top = Plane(Pnt(1, 1, 1), Vec(0, 0, 1)).bc("top")

    cube = left * right * front * back * bot * top
    geometry.Add(cube)
    return geometry


ngmesh = MakeGeometry().GenerateMesh(maxh=H_MAX)
mesh = Mesh(ngmesh)

In [3]:
fes_mag = VectorH1(
    mesh, order=1
)  # the finite element space for the magnetisation m_h^i
fes_mat = MatrixValued(
    H1(mesh, order=1), dim=3
)  # matrix FE space on the magnetic part
fes_disp = VectorH1(
    mesh, order=1, dirichlet="left"
)  # the finite element space for the displacement u_h^i
fesdivdiv = HDivDiv(mesh, order=1)**3

In [ ]:
myfunc = GridFunction(fesdivdiv)
print(myfunc)
print(div(myfunc))

In [ ]:
mycf = CF((x,0,0,
           0,0,0,
           0,0,0,
           y,0,0,
           0,0,0,
           0,0,0,
           z,0,0,
           0,0,0,
           0,0,0))
myfunc.Set(mycf)
mip = mesh(1,1,1)
with np.printoptions(precision=1,suppress=False):
    print(np.reshape(myfunc(mip),(3,3,3)))
    print(np.reshape(div(myfunc)(mip),(3,3)))